In [1]:
from rdkit import Chem
from rdkit.DataStructs import ConvertToNumpyArray
from rdkit.Chem import AllChem 
from rdkit.Chem import Draw  
from rdkit.Chem import Descriptors  
from rdkit.Chem import rdMolDescriptors  
from rdkit.Chem import MACCSkeys 
from rdkit.Chem import PandasTools  
import numpy as np 
import pandas as pd
from sklearn.preprocessing import StandardScaler
from scipy.sparse import csr_matrix

In [2]:
pwd

'/Users/u1536635/Downloads/notebooks'

In [3]:
df = pd.read_csv("/Users/u1536635/Downloads/COCONUT_2024_08_DrugDiscovery.tsv", sep="\t")
df

COCONUT_ID                                             SMILES  \
0       CNP0423157.1  C=CCC1=CC=C(O[C@H]2O[C@H]3[C@@H](O)[C@H](O)[C@...   
1       CNP0134552.1  CC(=O)O[C@H]1C[C@@H](OC(C)=O)C(C)(C)[C@]2(O)CC...   
2       CNP0537430.3  C/C=C1/C[N@@+](C)([O-])[C@H]2CC3=C(NC4=CC=CC=C...   
3       CNP0266805.4  CCCCCCCCCCCC[C@H](O)[C@@H]1CC[C@H]([C@H](O)CCC...   
4       CNP0495689.1  C=C1[C@@H](O)[C@]23C[C@@H](O)[C@H]1C[C@H]2[C@]...   
...              ...                                                ...   
695128  CNP0465073.1           CC1=C2C(=CC3=C1C(CO)=CS3)C(=O)CC[C@@H]2C   
695129  CNP0258161.1  CO[C@H]1O[C@H](CO)[C@@H](O)[C@@H](O)[C@H]1O[C@...   
695130  CNP0373415.0  COC1=CC2=C(C=C1OC)C(O)=C(C(=O)NCCCC1=CC=CC=C1)...   
695131  CNP0502978.1  O=C(O)CC(=O)O[C@H]1[C@H](O)[C@@H](O[C@@H]2O[C@...   
695132  CNP0370248.0  CCC1=CC2=C(C=C1OC(=O)C(C)C)OC(C(C)C)=C(C1=NC3=...   

        NPLikeness  QED_Drug_Likeness  SyntheticAccessibilityScore  
0         3.033571           0.131101                     7.461440  
1         1.907783           0.746106                     4.483797  
2         1.444057           0.363059                     5.157689  
3         1.810951           0.062377                     4.608241  
4         3.302002           0.592738                     6.115192  
...            ...                ...                          ...  
695128    0.743359           0.846839                     3.543758  
695129    2.517765           0.299695                     4.247294  
695130   -0.330031           0.545538                     2.137126  
695131    2.260449           0.050269                     6.016782  
695132   -0.640009           0.271060                     2.720885  

[695133 rows x 5 columns]

In [5]:
print(df['SyntheticAccessibilityScore'].describe())

count    695133.000000
mean          4.326502
std           1.464389
min           1.000000
25%           3.216241
50%           4.181297
75%           5.197380
max          10.000000
Name: SyntheticAccessibilityScore, dtype: float64


In [19]:
df_high_synth = df[df['SyntheticAccessibilityScore'] <= 5]
df_high_synth

COCONUT_ID                                             SMILES  \
1       CNP0134552.1  CC(=O)O[C@H]1C[C@@H](OC(C)=O)C(C)(C)[C@]2(O)CC...   
3       CNP0266805.4  CCCCCCCCCCCC[C@H](O)[C@@H]1CC[C@H]([C@H](O)CCC...   
5       CNP0027719.0                N#CCC1=CC=C(CC2=CC=C(CC#N)C=C2)C=C1   
6       CNP0332237.0          CC(C)C(=O)OCC(=O)C1=CC=C2OC(C)(C)C=CC2=C1   
8       CNP0579151.2  O=[N+]([O-])C1=CC=C(C[N@+]23CCCC[C@@H]2[C@H](C...   
...              ...                                                ...   
695127  CNP0353559.0          CC1=COC2=C(C)C3=C(C=C12)C1=C(CCC1)C(=O)O3   
695128  CNP0465073.1           CC1=C2C(=CC3=C1C(CO)=CS3)C(=O)CC[C@@H]2C   
695129  CNP0258161.1  CO[C@H]1O[C@H](CO)[C@@H](O)[C@@H](O)[C@H]1O[C@...   
695130  CNP0373415.0  COC1=CC2=C(C=C1OC)C(O)=C(C(=O)NCCCC1=CC=CC=C1)...   
695132  CNP0370248.0  CCC1=CC2=C(C=C1OC(=O)C(C)C)OC(C(C)C)=C(C1=NC3=...   

        NPLikeness  QED_Drug_Likeness  SyntheticAccessibilityScore  
1         1.907783           0.746106                     4.483797  
3         1.810951           0.062377                     4.608241  
5        -0.370620           0.829544                     1.947687  
6         1.111515           0.630126                     2.553692  
8         0.217385           0.528345                     3.780540  
...            ...                ...                          ...  
695127   -0.045445           0.575066                     2.650203  
695128    0.743359           0.846839                     3.543758  
695129    2.517765           0.299695                     4.247294  
695130   -0.330031           0.545538                     2.137126  
695132   -0.640009           0.271060                     2.720885  

[492790 rows x 5 columns]

In [20]:
# # Generate fingerprints for the entire filtered DataFrame
# from rdkit.DataStructs import BitVectToText

# high_synth_fingerprints = [
#     AllChem.GetMorganFingerprintAsBitVect(Chem.MolFromSmiles(smiles), 2, nBits=512)
#     for smiles in df_high_synth['SMILES']
# ]

# # Convert fingerprints to string representation
# high_synth_fingerprint_strings = [BitVectToText(fp) for fp in high_synth_fingerprints]

# # Add fingerprints as a new column to the filtered DataFrame
# df_high_synth['fingerprints'] = high_synth_fingerprint_strings

In [21]:
df_high_synth

COCONUT_ID                                             SMILES  \
1       CNP0134552.1  CC(=O)O[C@H]1C[C@@H](OC(C)=O)C(C)(C)[C@]2(O)CC...   
3       CNP0266805.4  CCCCCCCCCCCC[C@H](O)[C@@H]1CC[C@H]([C@H](O)CCC...   
5       CNP0027719.0                N#CCC1=CC=C(CC2=CC=C(CC#N)C=C2)C=C1   
6       CNP0332237.0          CC(C)C(=O)OCC(=O)C1=CC=C2OC(C)(C)C=CC2=C1   
8       CNP0579151.2  O=[N+]([O-])C1=CC=C(C[N@+]23CCCC[C@@H]2[C@H](C...   
...              ...                                                ...   
695127  CNP0353559.0          CC1=COC2=C(C)C3=C(C=C12)C1=C(CCC1)C(=O)O3   
695128  CNP0465073.1           CC1=C2C(=CC3=C1C(CO)=CS3)C(=O)CC[C@@H]2C   
695129  CNP0258161.1  CO[C@H]1O[C@H](CO)[C@@H](O)[C@@H](O)[C@H]1O[C@...   
695130  CNP0373415.0  COC1=CC2=C(C=C1OC)C(O)=C(C(=O)NCCCC1=CC=CC=C1)...   
695132  CNP0370248.0  CCC1=CC2=C(C=C1OC(=O)C(C)C)OC(C(C)C)=C(C1=NC3=...   

        NPLikeness  QED_Drug_Likeness  SyntheticAccessibilityScore  
1         1.907783           0.746106                     4.483797  
3         1.810951           0.062377                     4.608241  
5        -0.370620           0.829544                     1.947687  
6         1.111515           0.630126                     2.553692  
8         0.217385           0.528345                     3.780540  
...            ...                ...                          ...  
695127   -0.045445           0.575066                     2.650203  
695128    0.743359           0.846839                     3.543758  
695129    2.517765           0.299695                     4.247294  
695130   -0.330031           0.545538                     2.137126  
695132   -0.640009           0.271060                     2.720885  

[492790 rows x 5 columns]

In [22]:
print(df_high_synth.shape)

(492790, 5)


In [24]:
df_high_synth['NPLikeness'].describe()

count    492790.000000
mean          0.707648
std           1.303277
min          -3.533011
25%          -0.344575
50%           0.542078
75%           1.745978
max           4.070170
Name: NPLikeness, dtype: float64

In [25]:
df_high_np = df_high_synth[df_high_synth['NPLikeness'] >= 2]
df_high_np

COCONUT_ID                                             SMILES  \
21      CNP0138776.1  C=C(C(=O)O)[C@@H]1CC=C2CC[C@H](O)[C@H](C)[C@@]...   
22      CNP0169714.2  C/C1=C\CC[C@]2(C)O[C@H]2/C=C(/C(C)C)C(=O)C/C(C...   
25      CNP0478801.0                CC(C)=CCCC(C)=CCC=CC(C)(O)CCC=C(C)C   
35      CNP0247812.3  CC1=CC(=O)[C@H](O)[C@]2(C)CC[C@@H]3[C@H](OC(=O...   
36      CNP0272930.4  CC(=O)O[C@H]1CC[C@@]2(C)[C@H](CC[C@]3(C)[C@@H]...   
...              ...                                                ...   
695060  CNP0132551.1  CC(=O)O[C@@H]1C(CO)=CC(=O)[C@]2(C/C=C(\C)CC/C=...   
695063  CNP0410022.3     C=CC[C@@H]1C[C@@]2(O)C[C@H](C(C)(C)O)OC2=CC1=O   
695085  CNP0115213.1  C=C1C(=O)O[C@H]2[C@H]1[C@@H](OC(C)=O)C[C@@](C)...   
695115  CNP0139253.1  C/C(=C\CC[C@]1(C)CCC2=CC(O)=CC(C)=C2O1)C/C=C\[...   
695129  CNP0258161.1  CO[C@H]1O[C@H](CO)[C@@H](O)[C@@H](O)[C@H]1O[C@...   

        NPLikeness  QED_Drug_Likeness  SyntheticAccessibilityScore  
21        2.959673           0.584990                     4.393565  
22        2.588206           0.494854                     4.633424  
25        2.394389           0.506873                     3.689921  
35        3.089214           0.672931                     4.537491  
36        3.157218           0.284328                     4.721207  
...            ...                ...                          ...  
695060    2.671920           0.333616                     4.500346  
695063    2.892480           0.743535                     4.740360  
695085    3.494544           0.547436                     4.747529  
695115    2.535600           0.443949                     4.352752  
695129    2.517765           0.299695                     4.247294  

[94948 rows x 5 columns]

In [26]:
df_high_np['QED_Drug_Likeness'].describe()

count    94948.000000
mean         0.493676
std          0.181202
min          0.014873
25%          0.364492
50%          0.489954
75%          0.635081
max          0.942165
Name: QED_Drug_Likeness, dtype: float64

In [27]:
df_high_qed = df_high_np[df_high_np['QED_Drug_Likeness'] >= 0.4]
df_high_qed

COCONUT_ID                                             SMILES  \
21      CNP0138776.1  C=C(C(=O)O)[C@@H]1CC=C2CC[C@H](O)[C@H](C)[C@@]...   
22      CNP0169714.2  C/C1=C\CC[C@]2(C)O[C@H]2/C=C(/C(C)C)C(=O)C/C(C...   
25      CNP0478801.0                CC(C)=CCCC(C)=CCC=CC(C)(O)CCC=C(C)C   
35      CNP0247812.3  CC1=CC(=O)[C@H](O)[C@]2(C)CC[C@@H]3[C@H](OC(=O...   
43      CNP0508026.1  CC(C)=CCC/C(C)=C/COC1=CC=C2C(=O)[C@H](O)[C@@H]...   
...              ...                                                ...   
695009  CNP0178353.1  C=C[C@]1(C)C=C2C(=O)C[C@H]3[C@@](C)(CO)CCC[C@]...   
695047  CNP0112585.1  CC(C)=CC/C=C(\C)[C@H]1C/C=C(/C)CC/C=C(/C(=O)O)...   
695063  CNP0410022.3     C=CC[C@@H]1C[C@@]2(O)C[C@H](C(C)(C)O)OC2=CC1=O   
695085  CNP0115213.1  C=C1C(=O)O[C@H]2[C@H]1[C@@H](OC(C)=O)C[C@@](C)...   
695115  CNP0139253.1  C/C(=C\CC[C@]1(C)CCC2=CC(O)=CC(C)=C2O1)C/C=C\[...   

        NPLikeness  QED_Drug_Likeness  SyntheticAccessibilityScore  
21        2.959673           0.584990                     4.393565  
22        2.588206           0.494854                     4.633424  
25        2.394389           0.506873                     3.689921  
35        3.089214           0.672931                     4.537491  
43        2.048829           0.434478                     3.583235  
...            ...                ...                          ...  
695009    3.372805           0.772491                     4.607654  
695047    2.155840           0.518509                     4.175737  
695063    2.892480           0.743535                     4.740360  
695085    3.494544           0.547436                     4.747529  
695115    2.535600           0.443949                     4.352752  

[65723 rows x 5 columns]

In [28]:
# Generate fingerprints for the entire filtered DataFrame
from rdkit.DataStructs import BitVectToText

high_qed_fingerprints = [
    AllChem.GetMorganFingerprintAsBitVect(Chem.MolFromSmiles(smiles), 2, nBits=512)
    for smiles in df_high_qed['SMILES']
]

# Convert fingerprints to string representation
high_qed_fingerprint_strings = [BitVectToText(fp) for fp in high_qed_fingerprints]

# Add fingerprints as a new column to the filtered DataFrame
df_high_qed['fingerprints'] = high_qed_fingerprint_strings

[22:12:27] DEPRECATION WARNING: please use MorganGenerator
[22:12:27] DEPRECATION WARNING: please use MorganGenerator
[22:12:27] DEPRECATION WARNING: please use MorganGenerator
[22:12:27] DEPRECATION WARNING: please use MorganGenerator
[22:12:27] DEPRECATION WARNING: please use MorganGenerator
[22:12:27] DEPRECATION WARNING: please use MorganGenerator
[22:12:27] DEPRECATION WARNING: please use MorganGenerator
[22:12:27] DEPRECATION WARNING: please use MorganGenerator
[22:12:27] DEPRECATION WARNING: please use MorganGenerator
[22:12:27] DEPRECATION WARNING: please use MorganGenerator
[22:12:27] DEPRECATION WARNING: please use MorganGenerator
[22:12:27] DEPRECATION WARNING: please use MorganGenerator
[22:12:27] DEPRECATION WARNING: please use MorganGenerator
[22:12:27] DEPRECATION WARNING: please use MorganGenerator
[22:12:27] DEPRECATION WARNING: please use MorganGenerator
[22:12:27] DEPRECATION WARNING: please use MorganGenerator
[22:12:27] DEPRECATION WARNING: please use MorganGenerat

In [29]:
df_high_qed

COCONUT_ID                                             SMILES  \
21      CNP0138776.1  C=C(C(=O)O)[C@@H]1CC=C2CC[C@H](O)[C@H](C)[C@@]...   
22      CNP0169714.2  C/C1=C\CC[C@]2(C)O[C@H]2/C=C(/C(C)C)C(=O)C/C(C...   
25      CNP0478801.0                CC(C)=CCCC(C)=CCC=CC(C)(O)CCC=C(C)C   
35      CNP0247812.3  CC1=CC(=O)[C@H](O)[C@]2(C)CC[C@@H]3[C@H](OC(=O...   
43      CNP0508026.1  CC(C)=CCC/C(C)=C/COC1=CC=C2C(=O)[C@H](O)[C@@H]...   
...              ...                                                ...   
695009  CNP0178353.1  C=C[C@]1(C)C=C2C(=O)C[C@H]3[C@@](C)(CO)CCC[C@]...   
695047  CNP0112585.1  CC(C)=CC/C=C(\C)[C@H]1C/C=C(/C)CC/C=C(/C(=O)O)...   
695063  CNP0410022.3     C=CC[C@@H]1C[C@@]2(O)C[C@H](C(C)(C)O)OC2=CC1=O   
695085  CNP0115213.1  C=C1C(=O)O[C@H]2[C@H]1[C@@H](OC(C)=O)C[C@@](C)...   
695115  CNP0139253.1  C/C(=C\CC[C@]1(C)CCC2=CC(O)=CC(C)=C2O1)C/C=C\[...   

        NPLikeness  QED_Drug_Likeness  SyntheticAccessibilityScore  \
21        2.959673           0.584990                     4.393565   
22        2.588206           0.494854                     4.633424   
25        2.394389           0.506873                     3.689921   
35        3.089214           0.672931                     4.537491   
43        2.048829           0.434478                     3.583235   
...            ...                ...                          ...   
695009    3.372805           0.772491                     4.607654   
695047    2.155840           0.518509                     4.175737   
695063    2.892480           0.743535                     4.740360   
695085    3.494544           0.547436                     4.747529   
695115    2.535600           0.443949                     4.352752   

                                             fingerprints  
21      0000000000000000000000000000000001001000000100...  
22      0100000100000000000000000100100001001000000000...  
25      0000000000000000000000000000100001000010000000...  
35      0000100000000000000000000000000001001000000000...  
43      0000000000000000000000000010100001000010000000...  
...                                                   ...  
695009  0000100000000000000000000000000001001001000000...  
695047  0000100000000000000000000100000001000000000100...  
695063  0000100000000000000000000000000001001000000000...  
695085  0000000101010000000000000001001001011000000000...  
695115  0100000000000000000000000000000001001000000000...  

[65723 rows x 6 columns]

In [33]:
df_high_qed.to_csv('/Users/u1536635/Downloads/notebooks/high_qed_coconut.csv', index=None)

In [31]:
df_high_qed.iloc[4]

COCONUT_ID                                                          CNP0508026.1
SMILES                         CC(C)=CCC/C(C)=C/COC1=CC=C2C(=O)[C@H](O)[C@@H]...
NPLikeness                                                              2.048829
QED_Drug_Likeness                                                       0.434478
SyntheticAccessibilityScore                                             3.583235
fingerprints                   0000000000000000000000000010100001000010000000...
Name: 43, dtype: object